In [15]:
import pandas as pd
import numpy as np
import tensorflow as tf

import matplotlib.pyplot as plt
from imblearn.over_sampling import RandomOverSampler
from imblearn.under_sampling import RandomUnderSampler

import spacy

In [16]:
!python3 -m spacy download fr_core_news_sm

2023-05-02 18:54:54.707291: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
Defaulting to user installation because normal site-packages is not writeable
  Using cached https://github.com/explosion/spacy-models/releases/download/fr_core_news_sm-3.5.0/fr_core_news_sm-3.5.0-py3-none-any.whl (16.3 MB)
✔ Download and installation successful
You can now load the package via spacy.load('fr_core_news_sm')


In [17]:
nlp = spacy.load("fr_core_news_sm")
from nltk.corpus import stopwords
from nltk import download
download('stopwords')
stopWords = set(stopwords.words('french'))
print(stopWords)

{'été', 'étants', 'fûtes', 'soient', 'l', 'en', 'avions', 'aie', 'aviez', 'serait', 'fussiez', 'soyons', 'seras', 'auront', 'étions', 'ayons', 'étante', 'seriez', 'aies', 'fût', 'toi', 'sur', 'des', 'fûmes', 'ayant', 'j', 'étés', 'et', 'eussions', 'te', 'sont', 'c', 'du', 'ses', 'furent', 's', 'une', 'eut', 'étant', 'on', 'de', 'ont', 'son', 'nos', 'avaient', 'êtes', 'par', 'eurent', 'les', 'eues', 'mais', 'aux', 'dans', 'auras', 't', 'tes', 'serez', 'ayez', 'ils', 'aurions', 'soit', 'étaient', 'un', 'avons', 'es', 'pour', 'même', 'pas', 'était', 'aurait', 'soyez', 'mes', 'au', 'vous', 'fusse', 'eux', 'tu', 'fut', 'serions', 'as', 'ma', 'eu', 'eusses', 'sois', 'ai', 'aient', 'est', 'fusses', 'eusse', 'serais', 'ou', 'ta', 'avec', 'fussent', 'étais', 'étée', 'eûmes', 'ayantes', 'avait', 'votre', 'aurons', 'lui', 'ayants', 'serons', 'aura', 'à', 'ces', 'eus', 'ton', 'seront', 'le', 'eussent', 'la', 'seraient', 'avez', 'étantes', 'leur', 'qu', 'qui', 'avais', 'se', 'mon', 'serai', 'moi', 

[nltk_data] Downloading package stopwords to /home/el0h1m/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


# CNN

## Chargement des Données

In [18]:
# Données d'entrainement
train_data_complete = pd.read_csv("../data/allocine_genres_train.csv", sep=",")
train_data = train_data_complete[["titre", "synopsis", "genre"]]

# Données de test/validation
test_data_complete = pd.read_csv("../data/allocine_genres_test.csv", sep=",")
test_data = test_data_complete[["titre", "synopsis", "genre"]]

In [19]:
X = train_data.drop('genre', axis=1)
y = train_data['genre']

# Initialize the RandomOverSampler
ros = RandomOverSampler()
#ros = RandomUnderSampler()


# Perform oversampling
X_resampled, y_resampled = ros.fit_resample(X, y)

# Convert the resampled data back to a DataFrame
train_data = pd.concat([pd.DataFrame(X_resampled, columns=X.columns), pd.Series(y_resampled, name='genre')], axis=1)

Lister les classes et leur associer un identifiant unique. (Utile pour le plongement des mots et pour l'entraînement du CNN).

In [20]:
# Liste des genres
genre_name = sorted(train_data.genre.unique().flatten())
print("Genres:", genre_name)
print("Nombre d'exemplaires:", len(train_data))

# Identifiant unique par genre
genre2id = {genre_name[i]:i for i in range(len(genre_name))}
id2genre = {i:genre_name[i] for i in range(len(genre_name))}

Genres: ['biopic', 'comédie', 'documentaire', 'drame', 'historique', 'horreur', 'policier', 'romance', 'science fiction']
Nombre d'exemplaires: 4509


Remplacer les genres par la valeur numérique associée.

In [21]:
train_data = train_data.replace({"genre": genre2id})
train_data.head()

titre  \
0  Le Crime de l' Orient - Express   
1              12 hommes en colère   
2             Après moi le bonheur   
3         Les Lumières de la ville   
4        Les Chemins de la dignité   

                                            synopsis  genre  
0  En visite à Istanbul , le célèbre détective be...      6  
1  Un jeune homme d' origine modeste est accusé d...      3  
2  Lorsque Marie-Laure , mère de quatre jeunes en...      3  
3  Un vagabond s’ éprend d’ une belle et jeune ve...      7  
4  L' histoire vraie de Carl Brashear , premier A...      0

In [22]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(train_data[["titre", "synopsis"]],
                                                    train_data[["genre"]],
                                                    test_size=0.001,
                                                    random_state=12, # Random seed for shuffle
                                                    shuffle=False)

On combine le titre et le synopsis pour pouvoir les vectoriser par la suite.

In [23]:
X_train_titre = X_train.titre
X_train = X_train_titre + " " + X_train.synopsis

In [24]:
def preprocess(sentence) :
    list_w = nlp(sentence)
    list_w_clean = []
    res = []
    for token in list_w:
        if (token.text.lower() not in stopWords) and (token.text not in ["'",'-',',','.','…','...',':',';']):
            list_w_clean.append(token)
    for token in list_w_clean:
        res.append(token.lemma_.lower())
    print(res)
    return " ".join(res)

In [25]:
for i in range(len(X_train)):
    X_train[i] = preprocess(X_train[i])

['crime', 'orient', 'express', 'visite', 'istanbul', 'célèbre', 'détectiv', 'belge', 'hercule', 'poirot', 'embarqu', '’', 'orient', 'express', 'luxueux', 'train', 'relier', 'capitale', 'turc', 'calais', 'faire', 'connaissance', 'autre', 'passager', 'volubile', 'américaine', 'mme', 'hubbard', 'princesse', 'russe', 'dragomiroff', 'servant', 'hildegarde', 'séduisant', 'comte', 'hongrois', 'andrenyi', 'femme', 'matin', 'alors', 'train', 'immobiliser', 'sou', 'neige', 'passager', 'découvrir', 'effroi', 'm.', 'ratchett', 'antipathique', 'homme', '’', 'affaire', 'américain', 'avoir', 'froidement', 'assassiner', 'cabine', 'durer', 'nuit', 'hercule', 'poirot', 'celer', 'faire', 'aucun', 'doute', 'meurtrier', 'trouver', 'parmi', 'treize', 'personne', 'bord']
['12', 'homme', 'colère', 'jeune', 'homme', 'origine', 'modeste', 'accuser', 'meurtre', 'père', 'risque', 'peine', 'mort', 'jury', 'composer', 'douze', 'homme', 'retirer', 'délibérer', 'procéder', 'immédiatement', 'vote', 'onze', 'voter', 'c

In [26]:
X_train.head()

0    crime orient express visite istanbul célèbre d...
1    12 homme colère jeune homme origine modeste ac...
2    après bonheur lorsque marie-laure mère quatre ...
3    lumière ville vagabond ’ éprendre ’ belle jeun...
4    chemin dignité histoire vrai carl brashear pre...
dtype: object

In [27]:
y_train.head()

genre
0      6
1      3
2      3
3      7
4      0

In [54]:
print(X_train.shape)
print(X_train)
print(y_train.shape)

(3832, 200)
tf.Tensor(
[[ 554 1120  455 ...    0    0    0]
 [  69 7195 2001 ...    0    0    0]
 [ 141  842    1 ...    0    0    0]
 ...
 [4019  455 1233 ...    0    0    0]
 [1420 3328 4712 ...    0    0    0]
 [ 215  263   47 ...    0    0    0]], shape=(3832, 200), dtype=int64)
(4509,)


## Indexation du Vocabulaire

In [29]:
def get_vectorizer(documents, max_voc_size=8000, max_seq_length= 200, batch_size=64):
	vectorizer = tf.keras.layers.TextVectorization(max_tokens=max_voc_size, output_sequence_length=max_seq_length)
	# Création du jeu de données à partir de X_train et constitution de lots de 128 instances
	text_ds = tf.data.Dataset.from_tensor_slices(documents).batch(batch_size)
	# Création du vocabulaire à partir des données d'entrée
	vectorizer.adapt(text_ds)
	return vectorizer

In [30]:
keras_vectorizer = get_vectorizer(X_train)

2023-05-02 18:55:54.993883: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_0' with dtype string and shape [4504]
	 [[{{node Placeholder/_0}}]]


In [31]:
voc = keras_vectorizer.get_vocabulary()
print(len(voc))

8000


In [32]:
voc[:10]

['', '[UNK]', '’', 'avoir', 'plus', 'tout', 'faire', 'aller', 'vie', 'jeune']

In [33]:
word_index = dict(zip(voc, range(len(voc))))
print(word_index)

{'': 0, '[UNK]': 1, '’': 2, 'avoir': 3, 'plus': 4, 'tout': 5, 'faire': 6, 'aller': 7, 'vie': 8, 'jeune': 9, 'an': 10, 'femme': 11, 'homme': 12, 'deux': 13, 'ce': 14, 'alors': 15, 'pouvoir': 16, 'monde': 17, 'leur': 18, 'entrer': 19, 'jour': 20, 'nouveau': 21, 'histoire': 22, 'devoir': 23, 'devenir': 24, 'grand': 25, 'découvrir': 26, 'où': 27, 'petit': 28, 'être': 29, 'fille': 30, 'autre': 31, 'retrouver': 32, 'après': 33, 'décider': 34, 'voir': 35, 'année': 36, 'famille': 37, 'prendre': 38, 'seul': 39, 'sans': 40, 'celui': 41, 'premier': 42, 'ami': 43, 'comme': 44, 'passer': 45, 'dernier': 46, 'enfant': 47, 'amour': 48, 'temps': 49, 'père': 50, 'dont': 51, 'bien': 52, 'mettre': 53, 'film': 54, 'mort': 55, 'peu': 56, 'aussi': 57, 'ville': 58, 'depuis': 59, 'mère': 60, 'vivre': 61, 'sou': 62, 'rencontre': 63, 'trouver': 64, 'guerre': 65, 'the': 66, 'quand': 67, 'venir': 68, 'secret': 69, 'quelque': 70, 'contre': 71, 'jusqu': 72, 'nuit': 73, 'fils': 74, 'trois': 75, 'très': 76, 'jamais': 

In [34]:
print("Texte initial:", X_train.iloc[1])
output = keras_vectorizer([X_train.iloc[1]])
print("Vocabulaire dans le texte (15 premiers items):")
for v in output.numpy()[0, :15]:
    print(v, keras_vectorizer.get_vocabulary()[v])

Texte initial: 12 homme colère jeune homme origine modeste accuser meurtre père risque peine mort jury composer douze homme retirer délibérer procéder immédiatement vote onze voter coupable or décision devoir être prendre unanimité juré avoir voter non-coupabl sommé justifier expliquer avoir doute vie homme mérite quelque heure discussion emploie alors convaincre
Vocabulaire dans le texte (15 premiers items):
698 12
12 homme
821 colère
9 jeune
12 homme
279 origine
1116 modeste
970 accuser
191 meurtre
50 père
387 risque
380 peine
55 mort
7449 jury
1226 composer


## Chargement de Plongements de Mots Pré-entraînés

In [35]:
from gensim.models import KeyedVectors
model = KeyedVectors.load_word2vec_format("../embedding/frWiki_no_phrase_no_postag_700_cbow_cut100.bin", binary=True, unicode_errors="ignore")
model.most_similar("bonjour")

[('merci', 0.7507892847061157),
 ('bonsoir', 0.7450243830680847),
 ('votre', 0.5642200112342834),
 ('vous', 0.5538792014122009),
 ('remercier', 0.5396129488945007),
 ('avance', 0.5288880467414856),
 ('discuter', 0.5033395886421204),
 ('je', 0.49339333176612854),
 ('désoler', 0.4899965822696686),
 ('ici', 0.4887441396713257)]

In [36]:
model.key_to_index

{'</s>': 0,
 'de': 1,
 'la': 2,
 'à': 3,
 'le': 4,
 'et': 5,
 'être': 6,
 'en': 7,
 'les': 8,
 'un': 9,
 'une': 10,
 'avoir': 11,
 'il': 12,
 'dans': 13,
 'par': 14,
 'catégorie': 15,
 'pour': 16,
 'sur': 17,
 'que': 18,
 'se': 19,
 'qui': 20,
 'des': 21,
 'ce': 22,
 'avec': 23,
 'ne': 24,
 'son': 25,
 'an': 26,
 'plus': 27,
 'ou': 28,
 'pas': 29,
 'faire': 30,
 'elle': 31,
 'sa': 32,
 'pouvoir': 33,
 'pop': 34,
 'premier': 35,
 'mais': 36,
 'comme': 37,
 'cette': 38,
 'français': 39,
 'avancement': 40,
 'ses': 41,
 'je': 42,
 'on': 43,
 'deux': 44,
 'france': 45,
 'tout': 46,
 'aussi': 47,
 'lien': 48,
 'grand': 49,
 'année': 50,
 'autre': 51,
 'naissance': 52,
 'article': 53,
 'nom': 54,
 'après': 55,
 'voir': 56,
 'commune': 57,
 'état': 58,
 'ville': 59,
 'externe': 60,
 'y': 61,
 'paris': 62,
 'référence': 63,
 'entre': 64,
 'lui': 65,
 'même': 66,
 'source': 67,
 'sous': 68,
 'jean': 69,
 'lieu': 70,
 'leur': 71,
 'site': 72,
 'note': 73,
 'où': 74,
 'dont': 75,
 'film': 76,
 'ce

In [37]:
model["bonjour"]

array([-4.67579126e-01, -9.34297621e-01, -3.89060646e-01, -2.03962207e-01,
        6.24373436e-01,  5.58501959e-01, -7.94236243e-01,  9.47133780e-01,
       -7.85477459e-01, -4.23343748e-01, -3.78552794e-01,  9.85341787e-01,
       -9.94831264e-01,  7.94630885e-01, -3.72711942e-02, -1.31745422e+00,
       -2.15552300e-01, -1.77847058e-01,  4.44615424e-01,  2.40859807e-01,
       -1.34950832e-01,  2.62641966e-01,  7.27709755e-02, -4.39429581e-01,
        3.13311636e-01,  4.89237309e-01, -3.47837150e-01,  6.98559701e-01,
        3.06835920e-01,  8.79080057e-01, -5.81417084e-01, -3.37294281e-01,
        1.81973651e-01,  7.02408612e-01,  7.81347573e-01,  5.16828001e-01,
        2.21238777e-01, -4.01979834e-01, -3.04546077e-02,  5.94205201e-01,
        7.80208051e-01, -4.02492434e-01,  1.09107220e+00,  1.95819825e-01,
        1.20070234e-01,  4.59087253e-01,  6.24428272e-01,  3.55202556e-02,
       -1.29575109e+00, -5.80421746e-01,  4.97552425e-01,  3.83994550e-01,
       -6.25843883e-01,  

Le plongement pré-entrainé est de dimension 700.

In [38]:
len(model["bonjour"])

700

In [39]:
def load_embeddings(embeddings_model):
    embeddings_index = {}
    for word in list(embeddings_model.key_to_index.keys()):
        embeddings_index[word] = embeddings_model[word]
    print(f'{len(embeddings_index)} vecteurs de mots ont été lus')
    return embeddings_index

In [40]:
embeddings = load_embeddings(model)

39392 vecteurs de mots ont été lus


La cellule suivante permet de créer une matrice de plongements: une matrice où la ligne i correspond au plongement pré-entraîné pour le mot d'indice i dans le vocabulaire.

In [41]:
def get_embedding_matrix(vocabulary, embeddings_index, embedding_dim = 700):
  num_tokens = len(vocabulary)
  hits = 0
  misses = 0

  # Préparation de la matrice
  # Les mots qui ne se trouvent pas dans les plongements pré-entraînés seront 
  # représentés par des vecteurs dont toutes les composantes sont égales à 0,
  # y compris la représentation utilisée pour compléter les documents courts et
  # celle utilisée pour les mots inconnus [UNK]
  embedding_matrix = np.zeros((num_tokens, embedding_dim))
  for word, i in word_index.items():
      embedding_vector = embeddings_index.get(word)
      if embedding_vector is not None:
          embedding_matrix[i] = embedding_vector
          hits += 1
      else:
          misses += 1
  print(f'{hits} mots ont été trouvés dans les plongements pré-entraînés')
  print(f'{misses} sont absents')
  return embedding_matrix

In [42]:
# Construction de la matrice de plongements à partir du vocabulaire
embedding_matrix = get_embedding_matrix(voc, embeddings)

6049 mots ont été trouvés dans les plongements pré-entraînés
1951 sont absents


## Construction du CNN

In [43]:
from tensorflow.keras.layers import Embedding

def get_CNN_model(voc_size, embedding_matrix, embedding_dim=700):
  # Création du modèle
  int_sequences_input = tf.keras.Input(shape=(None,), dtype="int64")
  embedding_layer = Embedding(voc_size, embedding_dim, trainable=True,
      embeddings_initializer=tf.keras.initializers.Constant(embedding_matrix),
  )
  
  embedded_sequences = embedding_layer(int_sequences_input)
  x = tf.keras.layers.Conv1D(64, 5, activation="relu")(embedded_sequences)
  x = tf.keras.layers.MaxPooling1D(5)(x)
  x = tf.keras.layers.Conv1D(64, 5, activation="relu")(x)
  x = tf.keras.layers.GlobalMaxPooling1D()(x)
  x = tf.keras.layers.Dense(64, activation="relu")(x)
  x = tf.keras.layers.Dropout(0.5)(x)
  preds = tf.keras.layers.Dense(len(genre_name), activation="softmax")(x)
  model = tf.keras.Model(int_sequences_input, preds)
  return model

In [44]:
# Affichage de l'architecture du modèle
CNN_model = get_CNN_model(len(voc), embedding_matrix)
CNN_model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, None)]            0         
                                                                 
 embedding (Embedding)       (None, None, 700)         5600000   
                                                                 
 conv1d (Conv1D)             (None, None, 64)          224064    
                                                                 
 max_pooling1d (MaxPooling1D  (None, None, 64)         0         
 )                                                               
                                                                 
 conv1d_1 (Conv1D)           (None, None, 64)          20544     
                                                                 
 global_max_pooling1d (Globa  (None, 64)               0         
 lMaxPooling1D)                                              

## Entraînement du CNN

In [45]:
from sklearn import model_selection
from tensorflow.keras.callbacks import EarlyStopping # Early stopping to avoid over-fitting

# Fonction pour l'entraînement d'un modèle
def train_model(X, y, model_function, vectorizer, voc_size, embedding_matrix, embedding_dim=700, batch_size=64):
    
    # Early stopping callback
    early_stopping_callback = EarlyStopping(monitor="val_acc", restore_best_weights=True, patience=3)
    
    # Listes utilisées pour sauvegarder les résultats obtenus à chaque pli
    acc_per_fold = []
    loss_per_fold = []
    histories = []
    folds =  5 # 3
    stratkfold = model_selection.StratifiedKFold(n_splits=folds, shuffle=True, random_state=12)
    fold_no = 1
    for train, test in stratkfold.split(X, y):
        m_function = globals()[model_function]
        model = m_function(voc_size, embedding_matrix, embedding_dim)

        print('------------------------------------------------------------------------')
        print(f'Entraînement pour le pli {fold_no} ...')
        fold_x_train = vectorizer(X.iloc[train].to_numpy()).numpy()
        fold_x_val = vectorizer(X.iloc[test].to_numpy()).numpy()
        fold_y_train = y.iloc[train].to_numpy()
        fold_y_val = y.iloc[test].to_numpy()

        # Compilation du modèle : permet de préciser la fonction de perte et l'optimiseur
        # loss=sparse_categorical_crossentropy : entropie croisée, dans le cas où les 
        # classes cibles sont indiquées sous forme d'entiers. Il s'agira de minimiser
        # la perte pendant l'apprentissage
        # optimizer=rmsprop : l'optimiseur détermine la manière doit les poids seront
        # mis à jour pendant l'apprentissage
        model.compile(loss="sparse_categorical_crossentropy", optimizer="rmsprop", metrics=["acc"])
        # Entraînement sur 10 époque (la totalité du jeu de données est parcourue
        # 10 fois)
        history = model.fit(fold_x_train, fold_y_train, batch_size=batch_size, epochs=25, validation_data=(fold_x_val, fold_y_val), callbacks=[early_stopping_callback])
        histories.append(history)
        # Evaluation sur les données de validation
        scores = model.evaluate(fold_x_val, fold_y_val, verbose=0)
        print(f'Scores pour le pli {fold_no}: {model.metrics_names[0]} = {scores[0]:.2f};',
            f'{model.metrics_names[1]} = {scores[1]*100:.2f}%')
        acc_per_fold.append(scores[1] * 100)
        loss_per_fold.append(scores[0])
        fold_no = fold_no + 1

    # Affichage des scores moyens par pli
    print('---------------------------------------------------------------------')
    print('Scores par pli')
    for i in range(0, len(acc_per_fold)):
        print('---------------------------------------------------------------------')
        print(f'> Pli {i+1} - Loss: {loss_per_fold[i]:.2f}', f'- Accuracy: {acc_per_fold[i]:.2f}%')
    print('---------------------------------------------------------------------')
    print('Scores moyens pour tous les plis :')
    print(f'> Accuracy: {np.mean(acc_per_fold):.2f}', f'(+- {np.std(acc_per_fold):.2f})')
    print(f'> Loss: {np.mean(loss_per_fold):.2f}')
    print('---------------------------------------------------------------------')
    return histories

In [46]:
# Entraînement du modèle et récupération des résultats
CNN_histories = train_model(X_train, y_train, 'get_CNN_model', keras_vectorizer, len(voc), embedding_matrix)

------------------------------------------------------------------------
Entraînement pour le pli 1 ...
Epoch 1/25
57/57 [==============================] - 6s 100ms/step - loss: 2.0537 - acc: 0.2370 - val_loss: 1.7640 - val_acc: 0.3485
Epoch 2/25
57/57 [==============================] - 5s 94ms/step - loss: 1.3897 - acc: 0.5210 - val_loss: 1.2180 - val_acc: 0.6027
Epoch 3/25
57/57 [==============================] - 5s 92ms/step - loss: 0.9208 - acc: 0.7108 - val_loss: 1.0291 - val_acc: 0.6337
Epoch 4/25
57/57 [==============================] - 5s 90ms/step - loss: 0.6197 - acc: 0.8010 - val_loss: 1.0187 - val_acc: 0.6482
Epoch 5/25
57/57 [==============================] - 5s 87ms/step - loss: 0.4132 - acc: 0.8707 - val_loss: 0.6994 - val_acc: 0.7680
Epoch 6/25
24/57 [===========>..................] - ETA: 2s - loss: 0.2588 - acc: 0.9355

KeyboardInterrupt: 

In [47]:
import seaborn as sns
sns.set_theme(style="darkgrid")

def plot_results(histories):
    accuracy_data = []
    loss_data = []
    for i, h in enumerate(histories):
        acc = h.history['acc']
        val_acc = h.history['val_acc']
        loss = h.history['loss']
        val_loss = h.history['val_loss']
        for j in range(len(acc)):
            accuracy_data.append([i+1, j+1, acc[j], 'Entraînement'])
            accuracy_data.append([i+1, j+1, val_acc[j], 'Validation'])
            loss_data.append([i+1, j+1, loss[j], 'Entraînement'])
            loss_data.append([i+1, j+1, val_loss[j], 'Validation'])

    acc_df = pd.DataFrame(accuracy_data, columns=['Pli', 'Epoch', 'Accuracy', 'Données'])
    sns.relplot(data=acc_df, x='Epoch', y='Accuracy', hue='Pli', style='Données', kind='line')
    
    loss_df = pd.DataFrame(loss_data, columns=['Pli', 'Epoch', 'Perte', 'Données'])
    sns.relplot(data=loss_df, x='Epoch', y='Perte', hue='Pli', style='Données', kind='line')

In [48]:
plot_results(CNN_histories)

NameError: name 'CNN_histories' is not defined

## Test du Modèle

In [49]:
# Données d'entrainement
train_data_complete = pd.read_csv("../data/allocine_genres_train.csv", sep=",")
train_data = train_data_complete[["titre", "synopsis", "genre"]]

# Données de test/validation
test_data_complete = pd.read_csv("../data/allocine_genres_test.csv", sep=",")
test_data = test_data_complete[["titre", "synopsis", "genre"]]

In [50]:
X = train_data.drop('genre', axis=1)
y = train_data['genre']

# Initialize the RandomOverSampler
ros = RandomOverSampler()
#ros = RandomUnderSampler()


# Perform oversampling
X_resampled, y_resampled = ros.fit_resample(X, y)

# Convert the resampled data back to a DataFrame
train_data = pd.concat([pd.DataFrame(X_resampled, columns=X.columns), pd.Series(y_resampled, name='genre')], axis=1)

In [51]:
# Liste des genres
genre_name = sorted(train_data.genre.unique().flatten())
print("Genres:", genre_name)
print("Nombre d'exemplaires:", len(train_data))

# Identifiant unique par genre
genre2id = {genre_name[i]:i for i in range(len(genre_name))}
id2genre = {i:genre_name[i] for i in range(len(genre_name))}

train_data = train_data.replace({"genre": genre2id})
test_data = test_data.replace({"genre": genre2id})

Genres: ['biopic', 'comédie', 'documentaire', 'drame', 'historique', 'horreur', 'policier', 'romance', 'science fiction']
Nombre d'exemplaires: 4509


In [55]:
X_train_titre = train_data.titre
X_train = X_train_titre + " " + train_data.synopsis
for i in range(len(X_train)):
    X_train[i] = preprocess(X_train[i])
y_train = train_data.genre
X_train, X_val, y_train, y_val = train_test_split(X_train,y_train, test_size=0.15,shuffle=True)
X_train = keras_vectorizer(X_train)
X_val = keras_vectorizer(X_val)



X_test_titre = test_data.titre
X_test = X_test_titre + " " + test_data.synopsis
for i in range(len(X_test)):
    X_test[i] = preprocess(X_test[i])
X_test = keras_vectorizer(X_test)
y_test = test_data.genre

['crime', 'orient', 'express', 'visite', 'istanbul', 'célèbre', 'détectiv', 'belge', 'hercule', 'poirot', 'embarqu', '’', 'orient', 'express', 'luxueux', 'train', 'relier', 'capitale', 'turc', 'calais', 'faire', 'connaissance', 'autre', 'passager', 'volubile', 'américaine', 'mme', 'hubbard', 'princesse', 'russe', 'dragomiroff', 'servant', 'hildegarde', 'séduisant', 'comte', 'hongrois', 'andrenyi', 'femme', 'matin', 'alors', 'train', 'immobiliser', 'sou', 'neige', 'passager', 'découvrir', 'effroi', 'm.', 'ratchett', 'antipathique', 'homme', '’', 'affaire', 'américain', 'avoir', 'froidement', 'assassiner', 'cabine', 'durer', 'nuit', 'hercule', 'poirot', 'celer', 'faire', 'aucun', 'doute', 'meurtrier', 'trouver', 'parmi', 'treize', 'personne', 'bord']
['12', 'homme', 'colère', 'jeune', 'homme', 'origine', 'modeste', 'accuser', 'meurtre', 'père', 'risque', 'peine', 'mort', 'jury', 'composer', 'douze', 'homme', 'retirer', 'délibérer', 'procéder', 'immédiatement', 'vote', 'onze', 'voter', 'c

In [56]:
# Compile and train model
early_stopping_callback = EarlyStopping(monitor="val_acc", restore_best_weights=True, patience=3)
CNN_model.compile(loss="sparse_categorical_crossentropy", optimizer="rmsprop", metrics=["acc"])
CNN_model.fit(X_train, y_train, validation_split=0.1, batch_size=64, epochs=25, callbacks=[early_stopping_callback], validation_data=(X_val,y_val))

# Save model
#CNN_model.save("model")

Epoch 1/25
60/60 [==============================] - 5s 75ms/step - loss: 1.9761 - acc: 0.2727 - val_loss: 1.4729 - val_acc: 0.5155
Epoch 2/25
60/60 [==============================] - 4s 71ms/step - loss: 1.2636 - acc: 0.5676 - val_loss: 1.0366 - val_acc: 0.6765
Epoch 3/25
60/60 [==============================] - 4s 70ms/step - loss: 0.8217 - acc: 0.7260 - val_loss: 0.9581 - val_acc: 0.6677
Epoch 4/25
60/60 [==============================] - 5s 78ms/step - loss: 0.5673 - acc: 0.8202 - val_loss: 0.6660 - val_acc: 0.7843
Epoch 5/25
60/60 [==============================] - 5s 85ms/step - loss: 0.3694 - acc: 0.8849 - val_loss: 0.6448 - val_acc: 0.7843
Epoch 6/25
60/60 [==============================] - 5s 85ms/step - loss: 0.2487 - acc: 0.9295 - val_loss: 0.6286 - val_acc: 0.8080
Epoch 7/25
60/60 [==============================] - 5s 85ms/step - loss: 0.1731 - acc: 0.9515 - val_loss: 0.7382 - val_acc: 0.7858
Epoch 8/25
60/60 [==============================] - 5s 86ms/step - loss: 0.1250 - a

In [ ]:
# Load saved model
#CNN_model = tf.keras.models.load_model("model")

In [57]:
results = CNN_model.evaluate(X_test, y_test, batch_size=64)
print("test loss, test acc:", results)

12/12 [==============================] - 0s 24ms/step - loss: 1.5193 - acc: 0.5188
test loss, test acc: [1.5193102359771729, 0.5187760591506958]


In [58]:
# Vector of probability for each class
y_pred = CNN_model.predict(X_test)
print(y_pred[0])

# Vector of genre id with the highest probabillity
y_pred = np.argmax(y_pred, axis=1)
print(y_pred[0])

# Convert to dataframe
y_pred = pd.DataFrame(y_pred)

# Rename column and replace genre ids with genre names
y_pred.rename(columns={y_pred.columns[0]: "predicted_genre"}, inplace=True)
y_pred.replace({"predicted_genre": id2genre}, inplace=True)
y_pred

23/23 [==============================] - 0s 14ms/step
[0.00143096 0.56947654 0.00357397 0.30773163 0.00394617 0.0126231
 0.01111438 0.0641704  0.02593287]
1


predicted_genre
0            comédie
1    science fiction
2              drame
3              drame
4    science fiction
..               ...
714          comédie
715          comédie
716  science fiction
717            drame
718            drame

[719 rows x 1 columns]

In [59]:
test_data_complete["predicted_genre"] = y_pred
test_data_complete.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 719 entries, 0 to 718
Data columns (total 23 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   Unnamed: 0                719 non-null    int64  
 1   acteur_1                  719 non-null    object 
 2   acteur_2                  691 non-null    object 
 3   acteur_3                  686 non-null    object 
 4   allocine_id               719 non-null    int64  
 5   annee_prod                719 non-null    int64  
 6   annee_sortie              672 non-null    float64
 7   box_office_fr             438 non-null    float64
 8   couleur                   673 non-null    object 
 9   duree                     706 non-null    float64
 10  langues                   591 non-null    object 
 11  nationalite               719 non-null    object 
 12  nb_critiques_presse       514 non-null    float64
 13  nb_critiques_spectateurs  688 non-null    float64
 14  nb_notes_s

In [60]:
test_data_complete.to_csv("../data/test_results.csv")

In [61]:
print(len(test_data_complete[test_data_complete["genre"] == test_data_complete["predicted_genre"]]))

373


In [62]:
# Vector of probability for each class
y_pred = CNN_model.predict(X_test)
print(y_pred.shape)
print(y_pred[0])

# Vector of genre id with the highest probabillity
y_pred = np.argsort(y_pred, axis=1)
print(y_pred[0])
y_pred = np.flip(y_pred, axis=1)
print(y_pred.shape)
print(y_pred[0])

# Convert to dataframe
y_pred = pd.DataFrame(y_pred)

# Rename column and replace genre ids with genre names
y_pred.rename(columns={y_pred.columns[0]: "predicted_genre_1"}, inplace=True)
y_pred.replace({"predicted_genre_1": id2genre}, inplace=True)
y_pred.rename(columns={y_pred.columns[1]: "predicted_genre_2"}, inplace=True)
y_pred.replace({"predicted_genre_2": id2genre}, inplace=True)
y_pred.rename(columns={y_pred.columns[2]: "predicted_genre_3"}, inplace=True)
y_pred.replace({"predicted_genre_3": id2genre}, inplace=True)
y_pred.rename(columns={y_pred.columns[3]: "predicted_genre_4"}, inplace=True)
y_pred.replace({"predicted_genre_4": id2genre}, inplace=True)
y_pred.rename(columns={y_pred.columns[4]: "predicted_genre_5"}, inplace=True)
y_pred.replace({"predicted_genre_5": id2genre}, inplace=True)
y_pred.rename(columns={y_pred.columns[5]: "predicted_genre_6"}, inplace=True)
y_pred.replace({"predicted_genre_6": id2genre}, inplace=True)
y_pred.rename(columns={y_pred.columns[6]: "predicted_genre_7"}, inplace=True)
y_pred.replace({"predicted_genre_7": id2genre}, inplace=True)
y_pred.rename(columns={y_pred.columns[7]: "predicted_genre_8"}, inplace=True)
y_pred.replace({"predicted_genre_8": id2genre}, inplace=True)
y_pred.rename(columns={y_pred.columns[8]: "predicted_genre_9"}, inplace=True)
y_pred.replace({"predicted_genre_9": id2genre}, inplace=True)
y_pred

23/23 [==============================] - 0s 13ms/step
(719, 9)
[0.00143096 0.56947654 0.00357397 0.30773163 0.00394617 0.0126231
 0.01111438 0.0641704  0.02593287]
[0 2 4 6 5 8 7 3 1]
(719, 9)
[1 3 7 8 5 6 4 2 0]


predicted_genre_1 predicted_genre_2 predicted_genre_3 predicted_genre_4  \
0             comédie             drame           romance   science fiction   
1     science fiction          policier           horreur      documentaire   
2               drame           comédie           romance           horreur   
3               drame          policier           romance           comédie   
4     science fiction             drame           comédie           horreur   
..                ...               ...               ...               ...   
714           comédie   science fiction             drame           horreur   
715           comédie           horreur   science fiction           romance   
716   science fiction           horreur           comédie          policier   
717             drame           comédie           romance          policier   
718             drame           romance        historique           comédie   

    predicted_genre_5 predicted_genre_6 predicted_genre_7 predicted_genre_8  \
0             horreur          policier        historique      documentaire   
1             comédie        historique             drame            biopic   
2     science fiction          policier            biopic      documentaire   
3             horreur            biopic   science fiction      documentaire   
4            policier           romance        historique      documentaire   
..                ...               ...               ...               ...   
714      documentaire          policier           romance        historique   
715             drame          policier      documentaire        historique   
716             drame      documentaire           romance        historique   
717            biopic      documentaire        historique           horreur   
718            biopic   science fiction          policier           horreur   

    predicted_genre_9  
0              biopic  
1             romance  
2          historique  
3          historique  
4              biopic  
..                ...  
714            biopic  
715            biopic  
716            biopic  
717   science fiction  
718      documentaire  

[719 rows x 9 columns]

In [63]:
test_data_complete["predicted_genre_1"] = y_pred["predicted_genre_1"]
test_data_complete["predicted_genre_2"] = y_pred["predicted_genre_2"]
test_data_complete["predicted_genre_3"] = y_pred["predicted_genre_3"]
test_data_complete["predicted_genre_4"] = y_pred["predicted_genre_4"]
test_data_complete["predicted_genre_5"] = y_pred["predicted_genre_5"]
test_data_complete["predicted_genre_6"] = y_pred["predicted_genre_6"]
test_data_complete["predicted_genre_7"] = y_pred["predicted_genre_7"]
test_data_complete["predicted_genre_8"] = y_pred["predicted_genre_8"]
test_data_complete["predicted_genre_9"] = y_pred["predicted_genre_9"]

In [64]:
test_data_complete.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 719 entries, 0 to 718
Data columns (total 32 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   Unnamed: 0                719 non-null    int64  
 1   acteur_1                  719 non-null    object 
 2   acteur_2                  691 non-null    object 
 3   acteur_3                  686 non-null    object 
 4   allocine_id               719 non-null    int64  
 5   annee_prod                719 non-null    int64  
 6   annee_sortie              672 non-null    float64
 7   box_office_fr             438 non-null    float64
 8   couleur                   673 non-null    object 
 9   duree                     706 non-null    float64
 10  langues                   591 non-null    object 
 11  nationalite               719 non-null    object 
 12  nb_critiques_presse       514 non-null    float64
 13  nb_critiques_spectateurs  688 non-null    float64
 14  nb_notes_s

In [65]:
print(len(test_data_complete[(test_data_complete["genre"] == test_data_complete["predicted_genre_1"])
                             | (test_data_complete["genre"] == test_data_complete["predicted_genre_2"])
                            | (test_data_complete["genre"] == test_data_complete["predicted_genre_3"])]))

593
